# TESTE TRIGGOAI  

*git lfs ajustado, database.db consegue ser pushado

# 0: Importando Bibliotecas


In [51]:
import pandas as pd
import sqlalchemy
import plotly.express as px
import sklearn
import dash

# 1: Tratamento do dataset
Tratando as informações dos clientes

In [35]:
df_customers = pd.read_csv(r'dataset\olist_customers_dataset.csv', sep=',', encoding='utf-8')
df_customers.drop_duplicates(subset=['customer_id'], inplace=True)
df_customers.dropna(inplace=True)
df_customers['customer_city'] = df_customers['customer_city'].str.lower().str.strip().str.replace(' ', '_')

Tratando os dados de Geolocalização

In [4]:
df_geolocation = pd.read_csv(r'dataset\olist_geolocation_dataset.csv', sep=',', encoding='utf-8')
df_geolocation.drop_duplicates(inplace=True)
df_geolocation.dropna(inplace=True)
df_geolocation['geolocation_city'] = df_geolocation['geolocation_city'].str.lower().str.strip().str.replace(' ', '_')

Tratamento dados dos produtos comprados

In [5]:
df_order_item = pd.read_csv(r'dataset\olist_order_items_dataset.csv', sep=',', encoding='utf-8')
df_order_item.drop_duplicates(inplace=True)
df_order_item.dropna(inplace=True)
df_order_item['shipping_limit_date'] = pd.to_datetime(df_order_item['shipping_limit_date'], format='%Y-%m-%d %H:%M:%S')

order_item_float = [
    'price',
    'freight_value'
]

df_order_item[order_item_float] = df_order_item[order_item_float].astype(float)

Tratamento dos dados de pagamento


In [6]:
df_order_payment = pd.read_csv(r'dataset\olist_order_payments_dataset.csv', sep=',', encoding='utf-8')
df_order_payment.drop_duplicates(inplace=True)
df_order_payment.dropna(inplace=True)
df_order_payment = df_order_payment[df_order_payment['payment_sequential'] < 15]
df_order_payment['payment_type'] = df_order_payment['payment_type'].str.lower().str.strip().str.replace(' ', '_')
df_order_payment['payment_value'] = df_order_payment['payment_value'].astype(float)

order_payment_int = [
    'payment_sequential',
    'payment_installments'
]

df_order_payment[order_payment_int] = df_order_payment[order_payment_int].astype(int)   

Tratando os dados de reviews dos pedidos

In [7]:
df_order_reviews = pd.read_csv(r'dataset\olist_order_reviews_dataset.csv', sep=',', encoding='utf-8')
df_order_reviews.drop_duplicates(inplace=True)
df_order_reviews.dropna(subset=['review_id','order_id','review_score','review_creation_date','review_answer_timestamp'],inplace=True)
df_order_reviews['review_score'] = df_order_reviews['review_score'].astype(int)
df_order_reviews['review_comment_title'] = df_order_reviews['review_comment_title'].fillna('')
df_order_reviews['review_comment_message'] = df_order_reviews['review_comment_message'].fillna('')

reviews_datetime = [
    'review_creation_date',
    'review_answer_timestamp'
]
df_order_reviews[reviews_datetime] = df_order_reviews[reviews_datetime].apply(pd.to_datetime, format='%Y-%m-%d %H:%M:%S')

Tratando os dados de pedidos


In [8]:
df_orders = pd.read_csv(r'dataset\olist_orders_dataset.csv', sep=',', encoding='utf-8')
df_orders.drop_duplicates(inplace=True)
df_orders.dropna(inplace=True)
df_orders['order_id'] = df_orders['order_id'].str.strip()
df_orders['customer_id'] = df_orders['customer_id'].str.strip()
df_orders['order_status'] = df_orders['order_status'].str.strip().str.lower().astype('category')

orders_datetime = [
    'order_purchase_timestamp',
    'order_approved_at',
    'order_delivered_carrier_date',
    'order_delivered_customer_date',
    'order_estimated_delivery_date'
]
df_orders[orders_datetime] = df_orders[orders_datetime].apply(pd.to_datetime)



Tratando o dataset de produtos

In [9]:
df_products = pd.read_csv(r'dataset\olist_products_dataset.csv', sep=',', encoding='utf-8')
df_products.drop_duplicates(inplace=True)
df_products.dropna(inplace=True)
df_products['product_id'] = df_products['product_id'].str.strip()
df_products['product_category_name'] = df_products['product_category_name'].str.lower().str.strip().str.replace(' ', '_')

products_int = [
    'product_name_lenght',
    'product_description_lenght',
    'product_photos_qty',
    'product_weight_g',
    'product_length_cm',
    'product_height_cm'
]

df_products[products_int] = df_products[products_int].astype(int)

Tratando o dataset de vendedores

In [10]:
df_sellers = pd.read_csv(r'dataset\olist_sellers_dataset.csv', sep=',', encoding='utf-8')
df_sellers.drop_duplicates(inplace=True)
df_sellers.dropna(inplace=True)
df_sellers['seller_id'] = df_sellers['seller_id'].str.strip()
df_sellers['seller_zip_code_prefix'] = df_sellers['seller_zip_code_prefix'].astype(str)
df_sellers['seller_city'] = df_sellers['seller_city'].str.lower().str.strip().str.replace(' ', '_')
df_sellers['seller_state'] = df_sellers['seller_state'].str.strip()

# 2. Preparando o Modelo Relacional com SQLAlchemy

Criando a Engine do SQLAlchemy

In [11]:
engine = sqlalchemy.create_engine('sqlite:///datasets.db')
print('Conectando ao banco de dados...')
try:
    conn = engine.connect()
    print('Conexão estabelecida com sucesso!')
except sqlalchemy.exc.OperationalError as e:
    print(f'Erro ao conectar ao banco de dados: {e}')
    exit(1)

Conectando ao banco de dados...
Conexão estabelecida com sucesso!


Carregando os Dataframes no banco 

In [12]:
print('Criando tabelas no banco de dados...')
df_customers.to_sql('customers', con=engine, if_exists='replace', index=False)
df_geolocation.to_sql('geolocation', con=engine, if_exists='replace', index=False)
df_order_item.to_sql('order_item', con=engine, if_exists='replace', index=False)
df_order_payment.to_sql('order_payment', con=engine, if_exists='replace', index=False)
df_order_reviews.to_sql('order_reviews', con=engine, if_exists='replace', index=False)
df_orders.to_sql('orders', con=engine, if_exists='replace', index=False)
df_products.to_sql('products', con=engine, if_exists='replace', index=False)
df_sellers.to_sql('sellers', con=engine, if_exists='replace', index=False)
print('Tabelas criadas com sucesso!')
conn.close()

Criando tabelas no banco de dados...
Tabelas criadas com sucesso!


Criando Índices nas tabelas para melhor performance do código

In [13]:
with engine.connect() as conn:
    conn.execute(sqlalchemy.text('CREATE INDEX IF NOT EXISTS idx_orders_customer_id ON orders(customer_id)'))
    conn.execute(sqlalchemy.text('CREATE INDEX IF NOT EXISTS idx_orders_order_id ON orders(order_id)'))
    conn.execute(sqlalchemy.text('CREATE INDEX IF NOT EXISTS idx_order_item_product_id ON order_item(product_id)'))
    conn.execute(sqlalchemy.text('CREATE INDEX IF NOT EXISTS idx_order_item_product_id ON order_item(seller_id)'))
    conn.execute(sqlalchemy.text('CREATE INDEX IF NOT EXISTS idx_geolocation_geolocation_zip_code_prefix ON geolocation(geolocation_zip_code_prefix)'))

In [ ]:
query = """
SELECT a.order_id, b.customer_id, a.order_status, c.product_id, c.price
FROM orders a
JOIN customers b ON a.customer_id = b.customer_id
JOIN order_item c ON a.order_id = c.order_id
"""
df_joined = pd.read_sql(query, con=engine)


<bound method NDFrame.head of                                 order_id                       customer_id  \
0       00e7ee1b050b8499577073aeb2a297a1  06b8999e2fba1a1fbc88172c00ba8bc7   
1       29150127e6685892b6eab3eec79f59c7  18955e83d337fd6b2def6b18a428ac77   
2       b2059ed67ce144a36e2aa97d2c9e9ad2  4e7b3e00288586ebd08712fdd0374a03   
3       951670f92359f4fe4a63112aa7306eba  b2b6027bc5c5109e529d4dc6358b12c3   
4       6b7d50bd145f6fc7f33cebabd7e49d0f  4f2d8ab171c80ec8364f7c12e35b23ad   
...                                  ...                               ...   
110175  6760e20addcf0121e9d58f2f1ff14298  17ddf5dd5d51696bb3d7c6291687be6f   
110176  9ec0c8947d973db4f4e8dcf1fbfa8f1b  e7b71a9017aa05c9a7fd292d714858e8   
110177  fed4434add09a6f332ea398efd656a5c  5e28dfe12db7fb50a4b2f691faecea5e   
110178  e31ec91cea1ecf97797787471f98a8c2  56b18e2166679b8a959d72dd06da27f9   
110179  28db69209a75e59f20ccbb5c36a20b90  274fa6071e5e17fe303b9748641082c8   

       order_status              

## 3. Análise exploratória dos dados
Qual o volume de pedidos no mês? Existe sazonalidade nas vendas?

In [15]:
df_pedidos_mes = pd.read_sql('''
SELECT strftime('%m/%Y', order_purchase_timestamp) AS mes, COUNT(*) AS total_pedidos
FROM orders
GROUP BY mes
ORDER BY order_purchase_timestamp
''', con=engine)

df_pedidos_mes['total_pedidos'] = df_pedidos_mes['total_pedidos'].astype(int)

fig = px.line(df_pedidos_mes, x='mes', y='total_pedidos', title='Pedidos por Mês')
fig.update_layout(xaxis_title='Mês', yaxis_title='Total de Pedidos')
fig.show()


3.1: Qual a distribuição do tempo de entrega dos pedidos?

In [16]:
df_time_delivery = pd.read_sql('SELECT order_delivered_customer_date, order_purchase_timestamp FROM orders WHERE order_delivered_customer_date IS NOT NULL', con=engine)
df_time_delivery['tempo_entrega'] = (pd.to_datetime(df_time_delivery['order_delivered_customer_date']) - pd.to_datetime(df_time_delivery['order_purchase_timestamp'])).dt.days

df_time_delivery = df_time_delivery[df_time_delivery['tempo_entrega'] < 100] #Retirando um outlier

fig = px.histogram(df_time_delivery, x='tempo_entrega', nbins=30, title='Distribuição do Tempo de Entrega (em dias)')
fig.update_layout(xaxis_title='Dias para entrega', yaxis_title='Número de pedidos')
fig.show()


3.2: Quais são as categorias de produtos mais vendidas em termos de faturamento?

In [17]:
query = '''
SELECT
  p.product_category_name,
  SUM(o.price) AS faturamento_total
FROM
  order_item o
JOIN
  products p ON o.product_id = p.product_id
GROUP BY
  p.product_category_name
ORDER BY
  faturamento_total DESC
LIMIT 10;
'''

df_faturamento = pd.read_sql(query, con=engine)

fig = px.bar(df_faturamento, x='product_category_name', y='faturamento_total',
             title='Top 10 Categorias por Faturamento',
             labels={'product_category_name': 'Categoria', 'faturamento': 'Faturamento (R$)'},
             text_auto=True)
fig.show()


3.3: Quais estados brasileiros possuem o maior valor médio de pedido?

In [18]:
query = '''
SELECT
  c.customer_state,
  AVG(oi.total_order_value) AS valor_medio_pedido
FROM
  orders o
JOIN customers c ON o.customer_id = c.customer_id
JOIN (
  SELECT
    order_id,
    SUM(price + freight_value) AS total_order_value
  FROM
    order_item
  GROUP BY
    order_id
) oi ON o.order_id = oi.order_id
GROUP BY
  c.customer_state
ORDER BY
  valor_medio_pedido DESC
LIMIT 10;
'''

df_estado_valor_medio = pd.read_sql(query, con=engine)

fig = px.bar(
    df_estado_valor_medio,
    x='customer_state',
    y='valor_medio_pedido',
    title='Valor Médio de Pedido por Estado',
    labels={'customer_state': 'Estado', 'valor_medio_pedido': 'Valor Médio (R$)'}
)
fig.update_layout(xaxis_tickangle=-45)
fig.show()

# 4. Solução de Problemas de Negócio

In [19]:
query = '''
SELECT
  COUNT(*) AS total_clientes,
  SUM(CASE WHEN pedidos > 1 THEN 1 ELSE 0 END) AS clientes_recorrentes,
  ROUND(100.0 * SUM(CASE WHEN pedidos > 1 THEN 1 ELSE 0 END) * 1.0 / COUNT(*), 2) AS taxa_recorrencia
FROM (
  SELECT
    customer_id,
    COUNT(order_id) AS pedidos
  FROM orders
  GROUP BY customer_id
) 
'''

df_taxa_recorrencia = pd.read_sql(query, con=engine)

query = '''
SELECT
  customer_id,
  COUNT(order_id) AS pedidos
FROM orders
GROUP BY customer_id
'''

df_pedidos_cliente = pd.read_sql(query, con=engine)

recorrentes = df_pedidos_cliente[df_pedidos_cliente['pedidos'] > 1].shape[0]
nao_recorrentes = df_pedidos_cliente[df_pedidos_cliente['pedidos'] == 1].shape[0]

df_taxa_recorrencia = pd.DataFrame({
    'tipo': ['Recorrentes', 'Não Recorrentes'],
    'quantidade': [recorrentes, nao_recorrentes]
})

fig = px.bar(
    df_taxa_recorrencia,
    x='quantidade',
    y='tipo',
    orientation='h',
    title='Clientes Recorrentes vs Não Recorrentes',
    text='quantidade',
    color='tipo'
)
fig.update_layout(showlegend=False)
fig.show()


# 4.1: Predição de Atraso

In [40]:
df_predicao = pd.read_sql('SELECT * FROM orders', con=engine)

df_predicao = df.dropna(subset=[
    'order_delivered_customer_date',
    'order_estimated_delivery_date',
    'order_purchase_timestamp'
])

df_predicao['atraso'] = (df_predicao['order_delivered_customer_date'] > df_predicao['order_estimated_delivery_date']).astype(int)

df_predicao['order_delivered_customer_date'] = pd.to_datetime(df_predicao['order_delivered_customer_date'])
df_predicao['order_estimated_delivery_date'] = pd.to_datetime(df_predicao['order_estimated_delivery_date'])
df_predicao['order_purchase_timestamp'] = pd.to_datetime(df_predicao['order_purchase_timestamp'])

df_predicao['dias_entrega_real'] = (df_predicao['order_delivered_customer_date'] - df_predicao['order_purchase_timestamp']).dt.days
df_predicao['dias_estimado'] = (df_predicao['order_estimated_delivery_date'] - df_predicao['order_purchase_timestamp']).dt.days

df_predicao = df_predicao[(df_predicao['dias_entrega_real'] >= 0) & (df_predicao['dias_estimado'] >= 0)]

X = df_predicao[['dias_entrega_real', 'dias_estimado']]
y = df_predicao['atraso']

X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=42)

model = RandomForestClassifier(random_state=42)
model.fit(X_train, y_train)

y_pred = model.predict(X_test)
print(confusion_matrix(y_test, y_pred))
print(classification_report(y_test, y_pred))

[[17739     7]
 [   83  1464]]
              precision    recall  f1-score   support

           0       1.00      1.00      1.00     17746
           1       1.00      0.95      0.97      1547

    accuracy                           1.00     19293
   macro avg       1.00      0.97      0.98     19293
weighted avg       1.00      1.00      1.00     19293



17739: previu "no prazo" e estava certo.

7: previu "atrasado", mas estava "no prazo" → falso positivo.

83: previu "no prazo", mas estava "atrasado" → falso negativo.

1464: previu "atrasado" e estava certo.

Métricas:
Accuracy (acurácia): ≈ 1.00 → quase todas as previsões corretas.

Precision (precisão):

Classe 0: quase 1.00 → quando prevê "no prazo", quase sempre acerta.

Classe 1: alta → quando prevê "atrasado", geralmente está certo.


# 3.2: Segmentação de Clientes

In [ ]:

df_segmentacao = df_orders.merge(df_order_item, on='order_id', how='inner')

df_clientes = df_segmentacao.groupby('customer_id').agg({
    'order_id': 'nunique',            
    'price': 'sum',                   
    'freight_value': 'sum'           
}).reset_index()

df_clientes.columns = ['customer_id', 'qtd_pedidos', 'gasto_total', 'frete_total']
df_clientes['ticket_medio'] = df_clientes['gasto_total'] / df_clientes['qtd_pedidos']

X = df_clientes[['qtd_pedidos', 'gasto_total', 'frete_total', 'ticket_medio']]

# Normaliza os dados
scaler = sklearn.preprocessing.StandardScaler()
X_scaled = scaler.fit_transform(X)

# Aplica KMeans
kmeans = sklearn.cluster.KMeans(n_clusters=3, random_state=42)
df_clientes['cluster'] = kmeans.fit_predict(X_scaled)


fig = px.scatter_3d(
    df_clientes, x='qtd_pedidos', y='gasto_total', z='ticket_medio',
    color='cluster', title='Segmentação de Clientes'
)
fig.show()


# Análise:
Cluster 0: São clientes que compram pouco, mas gastam muito.
Estratégias: programas de fidelidade, prioridade em lançamentos e ofertas exclusivas para esse cluster de clientes.

Cluster 1: São clientes que realizam compras ocasionais e de baixo valor
Estratégias: Campanhas promocionais oferecendo cupons de desconto, ofertas de frete grátis e Remarketing com produtos parecidos aos que foram comprados.

Cluster 2: Clientes que compram com mais frequência com um valor médio estável
Estratégias: Assinaturas, benefícios progressivos baseado na frequência das compras e comunicações frequentes com os clientes.

# 3.3: Análise de satisfação


In [ ]:
query = '''
SELECT
  r.review_score,
  p.product_category_name,
  julianday(j.order_delivered_customer_date) - julianday(j.order_purchase_timestamp) AS tempo_entrega,
  (oi.price + oi.freight_value) AS valor_pedido
FROM orders j
JOIN order_reviews r ON j.order_id = r.order_id
JOIN order_item oi ON j.order_id = oi.order_id
JOIN products p ON oi.product_id = p.product_id
WHERE j.order_delivered_customer_date IS NOT NULL;

'''

df = pd.read_sql(query, con=engine)

df['tempo_entrega'] = df['tempo_entrega'].astype(float).round().astype(int)

corr_tempo = df['tempo_entrega'].corr(df['review_score'])
corr_valor = df['valor_pedido'].corr(df['review_score'])

top_categorias = nota_categoria.head(10).reset_index()

fig1 = px.bar(top_categorias, x='product_category_name', y='review_score',
              title='Top 10 Categorias com Melhor Nota Média',
              labels={'product_category_name':'Categoria', 'review_score':'Nota Média'})
fig1.show()

# Dispersão tempo_entrega x review_score
fig2 = px.scatter(df, x='tempo_entrega', y='review_score',
                  title='Relação entre Tempo de Entrega e Nota de Avaliação',
                  labels={'tempo_entrega':'Tempo de Entrega (dias)', 'review_score':'Nota de Avaliação'})
fig2.show()

# Dispersão valor_pedido x review_score
fig3 = px.scatter(df, x='valor_pedido', y='review_score',
                  title='Relação entre Valor do Pedido e Nota de Avaliação',
                  labels={'valor_pedido':'Valor do Pedido (R$)', 'review_score':'Nota de Avaliação'})
fig3.show()

Nota média por categoria:


# Análise

O tempo de entrega é o fator que mais impacta a satisfação do cliente, seguido da categoria do produto. O valor do pedido tem influência mínima.
Para melhorar a satisfação, seria necessário otimizar a logística e reavaliar todas as categorias com notas mais baixas.


# 4.0 Visualização e Dashboards

Evolução das vendas

In [80]:
query = '''
SELECT
  STRFTIME('%Y-%m', o.order_purchase_timestamp) AS mes,
  c.customer_state,
  p.product_category_name,
  SUM(oi.price + oi.freight_value) AS total_vendas
FROM orders o
JOIN order_item oi ON o.order_id = oi.order_id
JOIN customers c ON o.customer_id = c.customer_id
JOIN products p ON oi.product_id = p.product_id
WHERE o.order_status = 'delivered'
GROUP BY mes, c.customer_state, p.product_category_name
ORDER BY mes
'''

df = pd.read_sql_query(query, con=engine)
df['mes'] = pd.to_datetime(df['mes'])

app = dash.Dash(__name__)

app.layout = dash.html.Div([
    dash.html.H2("Evolução das Vendas com Filtros"),
    dash.dcc.Dropdown(
        id='estado-filter',
        options=[{'label': 'Todos', 'value': 'Todos'}] + [{'label': e, 'value': e} for e in sorted(df['customer_state'].unique())],
        value='Todos'
    ),
    dash.dcc.Dropdown(
        id='categoria-filter',
        options=[{'label': 'Todos', 'value': 'Todos'}] + [{'label': c, 'value': c} for c in sorted(df['product_category_name'].unique())],
        value='Todos'
    ),
    dash.dcc.Graph(id='grafico-vendas')
])

@app.callback(
    dash.Output('grafico-vendas', 'figure'),
    dash.Input('estado-filter', 'value'),
    dash.Input('categoria-filter', 'value')
)
def atualizar_grafico(estado, categoria):
    dff = df.copy()
    if estado != 'Todos':
        dff = dff[dff['customer_state'] == estado]
    if categoria != 'Todos':
        dff = dff[dff['product_category_name'] == categoria]

    dff_grouped = dff.groupby('mes')['total_vendas'].sum().reset_index()

    fig = px.line(dff_grouped, x='mes', y='total_vendas', title='Evolução das Vendas')
    fig.update_layout(xaxis_title='Mês', yaxis_title='Total Vendas')
    return fig

if __name__ == '__main__':
    app.run(debug=True)

Mapa de calor de vendas por estado

In [74]:
query = '''
SELECT
  c.customer_state,
  SUM(oi.price + oi.freight_value) AS total_vendas
FROM orders j
JOIN customers c ON j.customer_id = c.customer_id
JOIN order_item oi ON j.order_id = oi.order_id
WHERE j.order_status = 'delivered'
GROUP BY c.customer_state
ORDER BY total_vendas DESC
'''

df_mapa_calor = pd.read_sql_query(query, con=engine)

geojson_url = 'https://raw.githubusercontent.com/codeforgermany/click_that_hood/main/public/data/brazil-states.geojson'

fig = px.choropleth(
    df_mapa_calor,
    geojson=geojson_url,
    locations='customer_state',
    featureidkey='properties.sigla',
    color='total_vendas',
    color_continuous_scale='YlOrRd',
    title='Total de Vendas por Estado'
)

fig.update_geos(fitbounds="locations", visible=False)
fig.show()

Avaliação por Tempo de entrega

In [76]:
query = '''
SELECT
  r.review_score,
  JULIANDAY(o.order_delivered_customer_date) - JULIANDAY(o.order_purchase_timestamp) AS tempo_entrega
FROM orders o
JOIN order_reviews r ON o.order_id = r.order_id
WHERE o.order_delivered_customer_date IS NOT NULL
  AND r.review_score IS NOT NULL
'''

df_avaliacao = pd.read_sql_query(query, con=engine)

# Remover entregas negativas (casos com erro de data)
df_avaliacao = df_avaliacao[df_avaliacao['tempo_entrega'] >= 0]

# Scatter plot com tendência
fig = px.scatter(
    df_avaliacao,
    x='tempo_entrega',
    y='review_score',
    title='Avaliação vs Tempo de Entrega',
    labels={'tempo_entrega': 'Tempo de Entrega (dias)', 'review_score': 'Nota do Cliente'}
)
fig.show()

Avaliação Vendedores

In [ ]:
@app.callback(
    dash.Output('vendedores-desempenho', 'figure'),
    dash.Input('estado-dropdown', 'value')
)
def update_vendedores(estado):
    dff = df.copy()
    if estado:
        dff = dff[dff['customer_state'] == estado]
    
    vendedores = dff.groupby('seller_id').agg({
        'order_id': 'count',
        'review_score': 'mean',
        'tempo_entrega': 'mean'
    }).reset_index().rename(columns={
        'order_id': 'vendas',
        'review_score': 'avaliacao_media',
        'tempo_entrega': 'entrega_media'
    })
    
    fig = px.scatter(
        vendedores,
        x='entrega_media',
        y='avaliacao_media',
        size='vendas',
        hover_name='seller_id',
        title='Desempenho dos Vendedores'
    )
    return fig
